In [1]:
import pandas as pd
import os
os.getcwd()

'/Users/alrz-/Library/CloudStorage/OneDrive-Personal/Backup/Yield Curve Pricing'

In [2]:
# read the selected vectors
os.chdir("/Users/alrz-/Library/CloudStorage/OneDrive-Personal/Backup/Yield Curve Pricing/Data")
csv_file_path = 'Vectors_selected.csv'

Vectors_selected = pd.read_csv(csv_file_path, encoding='latin-1')

Vectors_selected.tail()

vectorid     productid  \
516  v111666248  3.310004e+09   
517  v111666249  3.310004e+09   
518     v730416  3.410014e+09   
519   v52299983  3.410014e+09   
520   v62295562  3.610010e+07   

                                           cubeTitleEn  \
516  Daily average foreign exchange rates in Canadi...   
517  Daily average foreign exchange rates in Canadi...   
518  Canada Mortgage and Housing Corporation, housi...   
519  Canada Mortgage and Housing Corporation, housi...   
520  Gross domestic product (GDP) at basic prices, ...   

                                    vector title more details  picked  \
516                   U.S. dollar, daily average          NaN     0.0   
517  Vietnamese dong, daily average (Terminated)          NaN     0.0   
518                               Housing starts          NaN     0.0   
519                                  Total units          NaN     0.0   
520                                          NaN          NaN     1.0   

     date_ok  dependant  
516      1.0        0.0  
517      0.0        0.0  
518      0.0        0.0  
519      0.0        0.0  
520      1.0        0.0

In [3]:
vectors_list = Vectors_selected[Vectors_selected['picked'] == 1]['vectorid'].dropna().tolist()
cleaned_list = [vector[1:] if vector.startswith('v') else vector for vector in vectors_list]
len(cleaned_list)

121

In [4]:
# this code retrieves data from STAT CANADA servers
from datetime import timedelta, date
os.chdir("/Users/alrz-/Library/CloudStorage/OneDrive-Personal/Backup/Yield Curve Pricing")
import STAT_CANADA

start_date=str(date.today()-timedelta(days=300 * 30))
data_by_range=STAT_CANADA.data_retrieve_by_range(cleaned_list,start_date=start_date)
data_by_range


date  value_80691332 releaseTime_80691332  value_80691333  \
0    1999-10-28             NaN                  NaN             NaN   
1    1999-10-29             NaN                  NaN             NaN   
2    1999-10-30             NaN                  NaN             NaN   
3    1999-10-31             NaN                  NaN             NaN   
4    1999-11-01             NaN                  NaN             NaN   
...         ...             ...                  ...             ...   
8996 2024-06-14             NaN                  NaN             NaN   
8997 2024-06-15             NaN                  NaN             NaN   
8998 2024-06-16             NaN                  NaN             NaN   
8999 2024-06-17             NaN                  NaN             NaN   
9000 2024-06-18             NaN                  NaN             NaN   

     releaseTime_80691333  value_80691334 releaseTime_80691334  \
0                     NaN             NaN                  NaN   
1                     NaN             NaN                  NaN   
2                     NaN             NaN                  NaN   
3                     NaN             NaN                  NaN   
4                     NaN             NaN                  NaN   
...                   ...             ...                  ...   
8996                  NaN             NaN                  NaN   
8997                  NaN             NaN                  NaN   
8998                  NaN             NaN                  NaN   
8999                  NaN             NaN                  NaN   
9000                  NaN             NaN                  NaN   

      value_80691335 releaseTime_80691335  value_80691336  ...  \
0                NaN                  NaN             NaN  ...   
1                NaN                  NaN             NaN  ...   
2                NaN                  NaN             NaN  ...   
3                NaN                  NaN             NaN  ...   
4                NaN                  NaN             NaN  ...   
...              ...                  ...             ...  ...   
8996             NaN                  NaN             NaN  ...   
8997             NaN                  NaN             NaN  ...   
8998             NaN                  NaN             NaN  ...   
8999             NaN                  NaN             NaN  ...   
9000             NaN                  NaN             NaN  ...   

     value_123263942  releaseTime_123263942 value_123263945  \
0                NaN                    NaN             NaN   
1                NaN                    NaN             NaN   
2                NaN                    NaN             NaN   
3                NaN                    NaN             NaN   
4                NaN                    NaN             NaN   
...              ...                    ...             ...   
8996             NaN                    NaN             NaN   
8997             NaN                    NaN             NaN   
8998             NaN                    NaN             NaN   
8999             NaN                    NaN             NaN   
9000             NaN                    NaN             NaN   

      releaseTime_123263945 value_108785713  releaseTime_108785713  \
0                       NaN             NaN                    NaN   
1                       NaN             NaN                    NaN   
2                       NaN             NaN                    NaN   
3                       NaN             NaN                    NaN   
4                       NaN             1.8       2024-05-21T08:30   
...                     ...             ...                    ...   
8996                    NaN             NaN                    NaN   
8997                    NaN             NaN                    NaN   
8998                    NaN             NaN                    NaN   
8999                    NaN             NaN                    NaN   
9000                    NaN      

In [5]:
# drop any f'value_{code}' where the first non Nan f'releaseTime_{code}' is year 2023 or later
for code in cleaned_list:
    releaseTime = f'releaseTime_{code}'
    value = f'value_{code}'

    # Convert the 'releaseTime' column to datetime
    data_by_range[releaseTime] = pd.to_datetime(data_by_range[releaseTime])

    # Drop NaN values and access the 'year' attribute
    releaseTime_year = data_by_range[releaseTime].dropna().dt.year

    # Check if the Series is not empty before accessing the element at index 0
    if len(releaseTime_year) > 0 and releaseTime_year.iloc[0] >= 2024:
        #print(f'dropping::: {code}')
        data_by_range.drop(columns=[value, releaseTime], inplace=True)

In [6]:

code='39051'
print(data_by_range[['date',f'value_{code}',f'releaseTime_{code}']][0:20])
data_by_range[['date',f'value_{code}',f'releaseTime_{code}']].to_csv('sample.csv',index=False)

         date  value_39051   releaseTime_39051
0  1999-10-28         5.90 2022-05-25 08:30:00
1  1999-10-29         5.75 2022-05-25 08:30:00
2  1999-10-30          NaN 2022-05-25 08:30:00
3  1999-10-31          NaN 2022-05-25 08:30:00
4  1999-11-01         5.71 2022-05-25 08:30:00
5  1999-11-02         5.72 2022-05-25 08:30:00
6  1999-11-03         5.78 2022-05-25 08:30:00
7  1999-11-04         5.69 2022-05-25 08:30:00
8  1999-11-05         5.72 2022-05-25 08:30:00
9  1999-11-06          NaN 2022-05-25 08:30:00
10 1999-11-07          NaN 2022-05-25 08:30:00
11 1999-11-08         5.77 2022-05-25 08:30:00
12 1999-11-09         5.78 2022-05-25 08:30:00
13 1999-11-10         5.78 2022-05-25 08:30:00
14 1999-11-11          NaN 2022-05-25 08:30:00
15 1999-11-12         5.71 2022-05-25 08:30:00
16 1999-11-13          NaN 2022-05-25 08:30:00
17 1999-11-14          NaN 2022-05-25 08:30:00
18 1999-11-15         5.68 2022-05-25 08:30:00
19 1999-11-16         5.76 2022-05-25 08:30:00


In [7]:
data_by_range

date  value_80691332 releaseTime_80691332  value_80691333  \
0    1999-10-28             NaN                  NaT             NaN   
1    1999-10-29             NaN                  NaT             NaN   
2    1999-10-30             NaN                  NaT             NaN   
3    1999-10-31             NaN                  NaT             NaN   
4    1999-11-01             NaN                  NaT             NaN   
...         ...             ...                  ...             ...   
8996 2024-06-14             NaN                  NaT             NaN   
8997 2024-06-15             NaN                  NaT             NaN   
8998 2024-06-16             NaN                  NaT             NaN   
8999 2024-06-17             NaN                  NaT             NaN   
9000 2024-06-18             NaN                  NaT             NaN   

     releaseTime_80691333  value_80691334 releaseTime_80691334  \
0                     NaT             NaN                  NaT   
1                     NaT             NaN                  NaT   
2                     NaT             NaN                  NaT   
3                     NaT             NaN                  NaT   
4                     NaT             NaN                  NaT   
...                   ...             ...                  ...   
8996                  NaT             NaN                  NaT   
8997                  NaT             NaN                  NaT   
8998                  NaT             NaN                  NaT   
8999                  NaT             NaN                  NaT   
9000                  NaT             NaN                  NaT   

      value_80691335 releaseTime_80691335  value_80691336  ... value_2710150  \
0                NaN                  NaT             NaN  ...           NaN   
1                NaN                  NaT             NaN  ...           NaN   
2                NaN                  NaT             NaN  ...           NaN   
3                NaN                  NaT             NaN  ...           NaN   
4                NaN                  NaT             NaN  ...         853.8   
...              ...                  ...             ...  ...           ...   
8996             NaN                  NaT             NaN  ...           NaN   
8997             NaN                  NaT             NaN  ...           NaN   
8998             NaN                  NaT             NaN  ...           NaN   
8999             NaN                  NaT             NaN  ...           NaN   
9000             NaN                  NaT             NaN  ...           NaN   

      releaseTime_2710150 value_123263908  releaseTime_123263908  \
0                     NaT             NaN                    NaT   
1                     NaT             NaN                    NaT   
2                     NaT             NaN                    NaT   
3                     NaT             NaN                    NaT   
4     2011-01-28 08:30:00             NaN                    NaT   
...                   ...             ...                    ...   
8996                  NaT             NaN                    NaT   
8997                  NaT             NaN                    NaT   
8998                  NaT             NaN                    NaT   
8999                  NaT             NaN                    NaT   
9000                  NaT             NaN                    NaT   

     value_123263939  releaseTime_123263939 value_123263942  \
0                NaN                    NaT             NaN   
1                NaN                    NaT             NaN   
2                NaN                    NaT             NaN   
3                NaN                    NaT             NaN   
4                NaN                    NaT             NaN   
...              ...                    ...             ...   
8996             NaN                    NaT             NaN   
8997             NaN                    NaT             NaN   
8998    

In [8]:
'''I need to make small adjustments as there are variables for which the data was available in the public but was uploaded
in stat can database later
examples are bond yields. the bond yields before 2022 are all uploaded on 2022 and then after that the data is updated regularly
'''

# I think I should just add one month of assurance to all vectors that are suddenly updated at a date
import pandas as pd
import numpy as np
import time as tm
import datetime as dt

# Get the column names
columns = data_by_range.columns

# Identify the columns that start with 'value' and 'releaseTime'
value_cols = [col for col in columns if col.startswith('value')]
release_cols = [col for col in columns if col.startswith('releaseTime')]

# Pair them up based on the vector_id
pairs = list(zip(value_cols, release_cols))

# Create a copy of the original DataFrame
data_by_range2 = data_by_range.copy()

# For each pair of columns
for value_col, release_col in pairs:
    # Convert 'releaseTime' to datetime if it's not already
    if data_by_range2[release_col].dtype != 'datetime64[ns]':
        data_by_range2[release_col] = pd.to_datetime(data_by_range2[release_col], errors='coerce')

    # Calculate the difference between the 'date' and 'releaseTime' for all rows
    diff = (data_by_range2[release_col]-data_by_range2['date'] ).dt.days

    # Create a mask for rows where this difference is more than 18 months
    mask = diff > 18*30

    # If the mask has any True values, print the vector ID
    if mask.any():
        vector_id = value_col.split('_')[-1]  # Assuming the vector_id is the part after the last underscore
        print(f"Applied operation for vector ID: {vector_id}")

    # Calculate the average of the differences for the last 18 months
    last_18_months_mask = (data_by_range2['date'] >= (data_by_range2['date'].max() - pd.DateOffset(months=18)))
    avg_diff = diff[last_18_months_mask].mean()
    # If avg_diff is NaN, skip this iteration
    if np.isnan(avg_diff):
        continue

    # Add this average to the 'date' for rows where the difference is more than 18 months
    new_dates = data_by_range2.loc[mask, 'date'] + pd.Timedelta(days=int(avg_diff))

    # Replace the 'releaseTime' for these rows with these calculated dates
    data_by_range2.loc[mask, release_col] = new_dates

Applied operation for vector ID: 80691332
Applied operation for vector ID: 80691333
Applied operation for vector ID: 80691334
Applied operation for vector ID: 80691335
Applied operation for vector ID: 80691336
Applied operation for vector ID: 122141
Applied operation for vector ID: 122148
Applied operation for vector ID: 122150
Applied operation for vector ID: 4429276
Applied operation for vector ID: 36459
Applied operation for vector ID: 36462
Applied operation for vector ID: 36463
Applied operation for vector ID: 122514
Applied operation for vector ID: 122529
Applied operation for vector ID: 122530
Applied operation for vector ID: 122531
Applied operation for vector ID: 122532
Applied operation for vector ID: 122533
Applied operation for vector ID: 122534
Applied operation for vector ID: 122535
Applied operation for vector ID: 122536
Applied operation for vector ID: 122537
Applied operation for vector ID: 122538
Applied operation for vector ID: 122539
Applied operation for vector ID:

In [9]:

value='v39051'
#diff = (data_by_range2[release_col]-data_by_range2['date']).dt.days
data_by_range[[f'date',f'value_{code}',f'releaseTime_{code}']].dropna()


date  value_39051   releaseTime_39051
0    1999-10-28         5.90 2022-05-25 08:30:00
1    1999-10-29         5.75 2022-05-25 08:30:00
4    1999-11-01         5.71 2022-05-25 08:30:00
5    1999-11-02         5.72 2022-05-25 08:30:00
6    1999-11-03         5.78 2022-05-25 08:30:00
...         ...          ...                 ...
8992 2024-06-10         3.99 2024-06-13 08:30:00
8993 2024-06-11         3.97 2024-06-14 08:30:00
8994 2024-06-12         3.91 2024-06-17 08:30:00
8995 2024-06-13         3.86 2024-06-18 08:30:00
8996 2024-06-14         3.83 2024-06-18 08:30:00

[6157 rows x 3 columns]

In [10]:
import re
'''
this part produces panel data corresponding to the most updated value of each variable up to the month end 
by checking with release time, I make sure the data is available upon trade, 
'''
# go over each variable and 
value_numbers = [re.search(r'value_(\d+)', var).group(1) for var in data_by_range2.columns if var.startswith('value')]

monthly_data=pd.DataFrame(index=pd.date_range(start=start_date,end=str(date.today()), freq='M'))

for v in value_numbers:
    temp=data_by_range2[[f'releaseTime_{v}', f'value_{v}']].copy()
    temp[f'releaseTime_{v}']=pd.to_datetime(data_by_range2[f'releaseTime_{v}'])
    temp.set_index(f'releaseTime_{v}', inplace=True)
    temp = temp.resample('D').last().ffill()
    monthly_data[f'value_{v}'] = temp[f'value_{v}']
    # if the last row is Nan, fill it with the last non-Nan value
    if pd.isna(monthly_data[f'value_{v}'].iloc[-1]):
        monthly_data[f'value_{v}'].iloc[-1] = monthly_data[f'value_{v}'].iloc[-2]

# drop nan columns from monthly data
monthly_data = monthly_data.dropna(axis=1, how='all')

In [12]:

value='39051'
#diff = (data_by_range2[release_col]-data_by_range2['date']).dt.days
monthly_data[[f'value_{value}']]

value_39051
1999-10-31          NaN
1999-11-30         5.83
1999-12-31         5.96
2000-01-31         6.20
2000-02-29         6.23
...                 ...
2024-01-31         3.88
2024-02-29         4.16
2024-03-31         4.16
2024-04-30         4.16
2024-05-31         4.28

[296 rows x 1 columns]

In [13]:
# Toronto stock exchange data is not updated anymore in Stats CAN
# use 
import yfinance as yf

# get all stock info
tsx = yf.Ticker("^GSPTSE")
tsx_hist = tsx.history(period="25y")['Close'].rename("Close_TSX")
tsx_hist.index = tsx_hist.index.tz_localize(None)
# Keep only the last day of the month observation
tsx_hist = tsx_hist.resample('M').last()

# Make the index year and month-based
tsx_hist.index = tsx_hist.index.to_period('M').strftime('%Y-%m')

#print(tsx_hist["Close"])

# get oil prices
oil = yf.Ticker("CL=F")
oil_hist = oil.history(period="25y")['Close'].rename("Close_Oil")
oil_hist.index = oil_hist.index.tz_localize(None)

oil_hist = oil_hist.resample('M').last()
oil_hist.index = oil_hist.index.to_period('M').strftime('%Y-%m')
#print(oil_hist["Close"])

# merge the data
merged_data = monthly_data.copy()
merged_data.index = merged_data.index.to_period('M').strftime('%Y-%m')

merged_data = merged_data.merge(oil_hist, left_index=True, right_index=True, how='left')
merged_data = merged_data.merge(tsx_hist, left_index=True, right_index=True, how='left')
merged_data

value_80691332  value_80691333  value_80691334  value_80691335  \
1999-10             NaN             NaN             NaN             NaN   
1999-11             NaN             NaN             NaN             NaN   
1999-12             NaN             NaN             NaN             NaN   
2000-01            3.00            7.35            8.05            8.25   
2000-02            3.00            7.35            8.05            8.25   
...                 ...             ...             ...             ...   
2024-01            2.25            7.84            7.04            6.89   
2024-02            2.25            7.84            6.99            6.84   
2024-03            2.25            7.84            6.99            6.84   
2024-04            2.25            7.84            6.99            6.84   
2024-05            2.25            7.84            6.99            6.84   

         value_80691336  value_122140  value_122141  value_122142  \
1999-10             NaN           NaN           NaN           NaN   
1999-11             NaN           NaN           NaN           NaN   
1999-12             NaN           NaN           NaN           NaN   
2000-01            5.35           NaN           NaN           NaN   
2000-02            5.35          6.02          5.89          6.62   
...                 ...           ...           ...           ...   
2024-01            3.45          4.01          5.44          3.78   
2024-02            3.45          4.01          5.44          3.91   
2024-03            3.45          4.01          5.44          4.26   
2024-04            3.45          4.01          5.44          4.18   
2024-05            3.45          4.01          5.41          4.64   

         value_122144  value_122148  ...  value_2710147  value_2710148  \
1999-10           NaN           NaN  ...            NaN            NaN   
1999-11           NaN           NaN  ...            NaN            NaN   
1999-12           NaN           NaN  ...          544.0         1707.3   
2000-01           NaN           NaN  ...          545.1         1742.9   
2000-02          5.73           8.5  ...          537.4         1666.5   
...               ...           ...  ...            ...            ...   
2024-01          5.38           8.5  ...          690.1         2281.5   
2024-02          5.40           8.5  ...          698.1         2226.8   
2024-03          5.37           8.5  ...          701.0         2197.4   
2024-04          5.37           8.5  ...          697.6         2192.3   
2024-05          5.37           8.5  ...          709.5         2211.1   

         value_2710149  value_2710150  value_123263908  value_123263939  \
1999-10            NaN            NaN              NaN              NaN   
1999-11            NaN            NaN              NaN              NaN   
1999-12          758.5          853.8              NaN              NaN   
2000-01          753.7          855.2              NaN              NaN   
2000-02          759.5          842.9              NaN              NaN   
...                ...            ...              ...              ...   
2024-01         1059.0         1362.7          55590.0          55602.0   
2024-02         1064.2         1386.5          55590.0          55602.0   
2024-03         1075.3         1392.9          55590.0          55602.0   
2024-04         1066.6         1406.8          55590.0          55602.0   
2024-05         1083.2         1402.5          56970.0          56343.0   

         value_123263942  value_123263945  Close_Oil     Close_TSX  
1999-10              NaN              NaN        NaN   7256.200195  
1999-11              NaN              NaN        NaN   7523.200195  
1999-12              NaN              NaN        NaN   8413.799805  
2000-01              NaN              NaN        NaN   8481.099609  
2000-02              NaN              NaN        NaN   9129.000000  
...                  ...              ...        ...           ...  
2024-0

In [13]:
#v='39051'
#monthly_data[[f'releaseTime_{v}', f'value_{v}']]
print(len(merged_data.columns))
#merged_data.columns
# convert to csv
merged_data.to_csv("merged_data.csv")

94


In [15]:
# there's variables with NaN values
# cehck them to see the severity
n=240

ind_data = merged_data.copy()

# Check for NaN values in the selected rows
rows_with_nan = ind_data.isna().any()
print(f"Columns with NaN values in the last {n} rows:   {sum(rows_with_nan)}")

Columns with NaN values in the last 240 rows:   93


In [16]:
# remove Nans
#ind_data.dropna(axis='columns', inplace=True)
len(ind_data.columns)

94

In [17]:
import pandas as pd
'''
I define dependet dataset which is yield curve 
value_39051
value_39052
value_39053
value_39054
value_39055
value_39056
value_39063
value_39064
value_39065
value_39066
value_39067
) 
data here

2_ I also need to remove the last observation from TSX after making it monthyl frequency
3- I need to add a month lead to the dependent variable 
'''

yield_list=['value_39051','value_39052','value_39053','value_39054','value_39055',
            'value_39056','value_39063','value_39064','value_39065','value_39066','value_39067']

# make data frame for yield curve which contains all the columns in the list
# that are in the ind_data data frame and lag it one month

yield_curve = ind_data[yield_list].shift(-1)

#yield_curve=yield_curve[:-1]

yield_curve.columns = [f"lead_{col}" for col in yield_curve.columns]
yield_curve['lead_value_39051']

1999-10    5.83
1999-11    5.96
1999-12    6.20
2000-01    6.23
2000-02    5.99
           ... 
2024-01    4.16
2024-02    4.16
2024-03    4.16
2024-04    4.28
2024-05     NaN
Name: lead_value_39051, Length: 296, dtype: float64

In [18]:
# create the lagged columns within the merged_data_normalized and ind_data_normalized
import pandas as pd

def create_lags(dataframe, n):
    lagged_dataframe = dataframe
    for column in dataframe.columns:
        for lag in range(1, n+1):
            lagged_dataframe[f"{column}_lag{lag}"] = dataframe[column].shift(lag)
    return lagged_dataframe

In [21]:
n = 6  # number of lags
ind_data_lagged = create_lags(ind_data, n)
print(len(ind_data_lagged.columns))

/var/folders/yc/wg49qgr50zq8bt1ws93sq3gr0000gp/T/ipykernel_19907/3595031459.py:8: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  lagged_dataframe[f"{column}_lag{lag}"] = dataframe[column].shift(lag)
/var/folders/yc/wg49qgr50zq8bt1ws93sq3gr0000gp/T/ipykernel_19907/3595031459.py:8: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  lagged_dataframe[f"{column}_lag{lag}"] = dataframe[column].shift(lag)
/var/folders/yc/wg49qgr50zq8bt1ws93sq3gr0000gp/T/ipykernel_19907/3595031459.py:8: PerformanceWarning: DataFrame is highly fragmented.  Thi

24346


/var/folders/yc/wg49qgr50zq8bt1ws93sq3gr0000gp/T/ipykernel_19907/3595031459.py:8: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  lagged_dataframe[f"{column}_lag{lag}"] = dataframe[column].shift(lag)
/var/folders/yc/wg49qgr50zq8bt1ws93sq3gr0000gp/T/ipykernel_19907/3595031459.py:8: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  lagged_dataframe[f"{column}_lag{lag}"] = dataframe[column].shift(lag)
/var/folders/yc/wg49qgr50zq8bt1ws93sq3gr0000gp/T/ipykernel_19907/3595031459.py:8: PerformanceWarning: DataFrame is highly fragmented.  Thi

In [ ]:
n=240

x=ind_data_lagged[-n-1:-1]
print(len(x.columns))

x2=x.dropna(axis='columns')
print(len(x2.columns))

y=yield_curve[-n-1:-1]
x2.to_csv("Data/x.csv")
y.to_csv("Data/y.csv")
print(os.getcwd())

658
588


'/Users/alrz-/Library/CloudStorage/OneDrive-Personal/Backup/Yield Curve Pricing'